---
### LSTM 3

7 day window, more epochs

In [94]:
early_stopping_cb = tf.keras.callbacks.EarlyStopping(monitor='loss', patience=5)

In [ ]:
window_size = 168  # 7 days
X_train, y_train = create_sequences(train, window_size)
X_test, y_test = create_sequences(test, window_size)
print(f'X_train shape: {X_train.shape}, y_train shape: {y_train.shape}')
print(f'X_test shape: {X_test.shape}, y_test shape: {y_test.shape}')
print(f'LSTM input shape: {X_train.shape[1], X_train.shape[2]}')

In [95]:
input_shape = (X_train.shape[1], X_train.shape[2])
lstm_units = 100
dropout = 0.2
output_units = 1

model_2 = Sequential()
model_2.add(LSTM(lstm_units, input_shape=input_shape))
model_2.add(Dropout(dropout))
model_2.add(Dense(output_units))
model_2.compile(optimizer='adam', loss='mean_squared_error')

model_2.summary()

Model: "sequential_4"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_4 (LSTM)               (None, 100)               40800     
                                                                 
 dropout_4 (Dropout)         (None, 100)               0         
                                                                 
 dense_4 (Dense)             (None, 1)                 101       
                                                                 
Total params: 40901 (159.77 KB)
Trainable params: 40901 (159.77 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [96]:
history_2 = model_2.fit(X_train, y_train,
                        epochs=100,
                        batch_size=32,
                        validation_data=(X_test, y_test),
                        callbacks=[early_stopping_cb],
                        shuffle=False
                        )

Epoch 1/100
874/874 [==============================] - 8s 7ms/step - loss: 0.0117 - val_loss: 0.0027
Epoch 2/100
874/874 [==============================] - 5s 6ms/step - loss: 0.0035 - val_loss: 0.0017
Epoch 3/100
874/874 [==============================] - 5s 6ms/step - loss: 0.0024 - val_loss: 0.0013
Epoch 4/100
874/874 [==============================] - 5s 6ms/step - loss: 0.0019 - val_loss: 0.0010
Epoch 5/100
874/874 [==============================] - 5s 6ms/step - loss: 0.0017 - val_loss: 9.8768e-04
Epoch 6/100
874/874 [==============================] - 5s 6ms/step - loss: 0.0015 - val_loss: 8.8220e-04
Epoch 7/100
874/874 [==============================] - 6s 7ms/step - loss: 0.0014 - val_loss: 8.6461e-04
Epoch 8/100
874/874 [==============================] - 5s 6ms/step - loss: 0.0013 - val_loss: 8.5392e-04
Epoch 9/100
874/874 [==============================] - 6s 7ms/step - loss: 0.0012 - val_loss: 7.7025e-04
Epoch 10/100
874/874 [==============================] - 5s 6ms/step - l

In [97]:
fig = px.line(history_2.history,
              labels={'value': 'Loss',
                      'index': 'Epoch'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [98]:
train_preds_2 = model_2.predict(X_train[window_size:])
test_preds_2 = model_2.predict(X_test[window_size:])

213/213 [==============================] - 1s 3ms/step


In [99]:
preds_2 = np.concatenate((train_preds_2, test_preds_2), axis=0)
preds_2 = scaler.inverse_transform(preds_2)
preds_2 = preds_2.reshape(-1)

y_train_2 = scaler.inverse_transform(y_train)
y_test_2 = scaler.inverse_transform(y_test)
y_2 = np.concatenate((y_train_2[window_size:].reshape(-1), y_test_2[window_size:].reshape(-1)), axis=0)

results_2_df = energy_df['time'][2 * window_size:train.shape[0]]

results_2_df = pd.DataFrame(np.concatenate([energy_df['time'][2 * window_size:train.shape[0]],
                                            energy_df['time'][train.shape[0] + 2 * window_size:]]))
results_2_df.columns = ['time']
results_2_df['preds'] = preds_2
results_2_df['y'] = y_2

In [100]:
fig = px.line(results_2_df, x='time', y=['preds', 'y'],
              labels={'value': 'Total Demand',
                      'time': 'time'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [101]:
fig = px.line(results_2_df[-300:], x='time', y=['preds', 'y'],
              labels={'value': 'Total Demand',
                      'time': 'time'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [102]:
print(f'MAPE: {mean_absolute_percentage_error(y_2, preds_2):.2%}')
print(f'MSE:  {(mean_squared_error(y_2, preds_2)**0.5):.0f}')

MAPE: 1.07%
MSE:  486


---
### LSTM 4

Add a Dense layer

In [103]:
early_stopping_cb = tf.keras.callbacks.EarlyStopping(monitor='loss', patience=5)

In [104]:
window_size = 168  # 7 days
X_train, y_train = create_sequences(train, window_size)
X_test, y_test = create_sequences(test, window_size)
print(f'X_train shape: {X_train.shape}, y_train shape: {y_train.shape}')
print(f'X_test shape: {X_test.shape}, y_test shape: {y_test.shape}')
print(f'LSTM input shape: {X_train.shape[1], X_train.shape[2]}')

X_train shape: (27883, 168, 1), y_train shape: (27883, 1)
X_test shape: (6845, 168, 1), y_test shape: (6845, 1)
LSTM input shape: (168, 1)


In [106]:
input_shape = (X_train.shape[1], X_train.shape[2])
lstm_units = 100
dropout = 0.2
output_units = 1

model_2 = Sequential()
model_2.add(LSTM(lstm_units, input_shape=input_shape))
model_2.add(Dense(100))
model_2.add(Dropout(dropout))
model_2.add(Dense(output_units))
model_2.compile(optimizer='adam', loss='mean_squared_error',)

model_2.summary()

Model: "sequential_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_5 (LSTM)               (None, 100)               40800     
                                                                 
 dense_5 (Dense)             (None, 100)               10100     
                                                                 
 dropout_5 (Dropout)         (None, 100)               0         
                                                                 
 dense_6 (Dense)             (None, 1)                 101       
                                                                 
Total params: 51001 (199.22 KB)
Trainable params: 51001 (199.22 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [107]:
history_2 = model_2.fit(X_train, y_train,
                        epochs=100,
                        batch_size=32,
                        validation_data=(X_test, y_test),
                        callbacks=[early_stopping_cb],
                        shuffle=False
                        )

Epoch 1/100
872/872 [==============================] - 9s 9ms/step - loss: 0.0061 - val_loss: 0.0017
Epoch 2/100
872/872 [==============================] - 7s 8ms/step - loss: 0.0021 - val_loss: 0.0012
Epoch 3/100
872/872 [==============================] - 7s 8ms/step - loss: 0.0017 - val_loss: 0.0010
Epoch 4/100
872/872 [==============================] - 7s 8ms/step - loss: 0.0015 - val_loss: 0.0010
Epoch 5/100
872/872 [==============================] - 7s 8ms/step - loss: 0.0014 - val_loss: 9.3442e-04
Epoch 6/100
872/872 [==============================] - 7s 8ms/step - loss: 0.0013 - val_loss: 9.2799e-04
Epoch 7/100
872/872 [==============================] - 7s 8ms/step - loss: 0.0012 - val_loss: 8.6570e-04
Epoch 8/100
872/872 [==============================] - 7s 8ms/step - loss: 0.0011 - val_loss: 8.6545e-04
Epoch 9/100
872/872 [==============================] - 7s 8ms/step - loss: 0.0011 - val_loss: 7.8698e-04
Epoch 10/100
872/872 [==============================] - 7s 8ms/step - l

In [108]:
fig = px.line(history_2.history,
              labels={'value': 'Loss',
                      'index': 'Epoch'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [109]:
train_preds_2 = model_2.predict(X_train[window_size:])
test_preds_2 = model_2.predict(X_test[window_size:])

209/209 [==============================] - 1s 3ms/step


In [110]:
preds_2 = np.concatenate((train_preds_2, test_preds_2), axis=0)
preds_2 = scaler.inverse_transform(preds_2)
preds_2 = preds_2.reshape(-1)

y_train_2 = scaler.inverse_transform(y_train)
y_test_2 = scaler.inverse_transform(y_test)
y_2 = np.concatenate((y_train_2[window_size:].reshape(-1), y_test_2[window_size:].reshape(-1)), axis=0)

results_2_df = energy_df['time'][2 * window_size:train.shape[0]]

results_2_df = pd.DataFrame(np.concatenate([energy_df['time'][2 * window_size:train.shape[0]],
                                            energy_df['time'][train.shape[0] + 2 * window_size:]]))
results_2_df.columns = ['time']
results_2_df['preds'] = preds_2
results_2_df['y'] = y_2

In [111]:
fig = px.line(results_2_df, x='time', y=['preds', 'y'],
              labels={'value': 'Total Demand',
                      'time': 'time'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [112]:
fig = px.line(results_2_df[-300:], x='time', y=['preds', 'y'],
              labels={'value': 'Total Demand',
                      'time': 'time'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [113]:
print(f'MAPE: {mean_absolute_percentage_error(y_2, preds_2):.2%}')
print(f'MSE:  {(mean_squared_error(y_2, preds_2)**0.5):.0f}')

MAPE: 1.10%
MSE:  479


---
### LSTM 5

Add exponential decay

In [131]:
early_stopping_cb = tf.keras.callbacks.EarlyStopping(monitor='loss', patience=5)

In [142]:
initial_learning_rate = 0.001
lr_schedule = tf.keras.optimizers.schedules.ExponentialDecay(initial_learning_rate,
                                                             decay_steps=872,
                                                             decay_rate=0.98)

optimizer = tf.keras.optimizers.Adam(learning_rate=lr_schedule)

In [143]:
window_size = 168  # 7 days
X_train, y_train = create_sequences(train, window_size)
X_test, y_test = create_sequences(test, window_size)
print(f'X_train shape: {X_train.shape}, y_train shape: {y_train.shape}')
print(f'X_test shape: {X_test.shape}, y_test shape: {y_test.shape}')
print(f'LSTM input shape: {X_train.shape[1], X_train.shape[2]}')

X_train shape: (27883, 168, 1), y_train shape: (27883, 1)
X_test shape: (6845, 168, 1), y_test shape: (6845, 1)
LSTM input shape: (168, 1)


In [144]:
input_shape = (X_train.shape[1], X_train.shape[2])
lstm_units = 100
dropout = 0.2
output_units = 1

model_2 = Sequential()
model_2.add(LSTM(lstm_units, input_shape=input_shape))
model_2.add(Dense(100))
model_2.add(Dropout(dropout))
model_2.add(Dense(output_units))
model_2.compile(optimizer=optimizer, loss='mean_squared_error',)

model_2.summary()

Model: "sequential_7"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_7 (LSTM)               (None, 100)               40800     
                                                                 
 dense_9 (Dense)             (None, 100)               10100     
                                                                 
 dropout_7 (Dropout)         (None, 100)               0         
                                                                 
 dense_10 (Dense)            (None, 1)                 101       
                                                                 
Total params: 51001 (199.22 KB)
Trainable params: 51001 (199.22 KB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________


In [145]:
history_2 = model_2.fit(X_train, y_train,
                        epochs=100,
                        batch_size=32,
                        validation_data=(X_test, y_test),
                        callbacks=[early_stopping_cb],
                        shuffle=False
                        )

Epoch 1/100
872/872 [==============================] - 10s 10ms/step - loss: 0.0064 - val_loss: 0.0016
Epoch 2/100
872/872 [==============================] - 8s 9ms/step - loss: 0.0020 - val_loss: 0.0015
Epoch 3/100
872/872 [==============================] - 8s 9ms/step - loss: 0.0017 - val_loss: 0.0011
Epoch 4/100
872/872 [==============================] - 8s 9ms/step - loss: 0.0015 - val_loss: 9.8936e-04
Epoch 5/100
872/872 [==============================] - 8s 9ms/step - loss: 0.0014 - val_loss: 9.6060e-04
Epoch 6/100
872/872 [==============================] - 8s 9ms/step - loss: 0.0013 - val_loss: 9.4303e-04
Epoch 7/100
872/872 [==============================] - 8s 9ms/step - loss: 0.0012 - val_loss: 8.8644e-04
Epoch 8/100
872/872 [==============================] - 8s 9ms/step - loss: 0.0012 - val_loss: 8.6420e-04
Epoch 9/100
872/872 [==============================] - 8s 9ms/step - loss: 0.0011 - val_loss: 8.4058e-04
Epoch 10/100
872/872 [==============================] - 8s 9ms/st

In [146]:
fig = px.line(history_2.history,
              labels={'value': 'Loss',
                      'index': 'Epoch'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [147]:
train_preds_2 = model_2.predict(X_train[window_size:])
test_preds_2 = model_2.predict(X_test[window_size:])

209/209 [==============================] - 1s 4ms/step


In [148]:
preds_2 = np.concatenate((train_preds_2, test_preds_2), axis=0)
preds_2 = scaler.inverse_transform(preds_2)
preds_2 = preds_2.reshape(-1)

y_train_2 = scaler.inverse_transform(y_train)
y_test_2 = scaler.inverse_transform(y_test)
y_2 = np.concatenate((y_train_2[window_size:].reshape(-1), y_test_2[window_size:].reshape(-1)), axis=0)

results_2_df = energy_df['time'][2 * window_size:train.shape[0]]

results_2_df = pd.DataFrame(np.concatenate([energy_df['time'][2 * window_size:train.shape[0]],
                                            energy_df['time'][train.shape[0] + 2 * window_size:]]))
results_2_df.columns = ['time']
results_2_df['preds'] = preds_2
results_2_df['y'] = y_2

In [149]:
fig = px.line(results_2_df, x='time', y=['preds', 'y'],
              labels={'value': 'Total Demand',
                      'time': 'time'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [150]:
fig = px.line(results_2_df[-300:], x='time', y=['preds', 'y'],
              labels={'value': 'Total Demand',
                      'time': 'time'})
fig.update_layout(legend=dict(title='',
                              yanchor="top", y=0.99,
                              xanchor="right", x=0.99))
fig.show()

In [151]:
print(f'MAPE: {mean_absolute_percentage_error(y_2, preds_2):.2%}')
print(f'MSE:  {(mean_squared_error(y_2, preds_2)**0.5):.0f}')

MAPE: 1.03%
MSE:  465


---
## 5. Results

#### Baseline

The first model is a simple 30 period moving average that I used to establish an easily beatable baseline. Looking at the zoomed in plot of predicted vs actuals, we can see that this model captures the macro trend fairly well, but completely fails to capture the magnitude of the day-to-day and intra-day fluctuations in power demand. This would be useful for predicting trends in demand on a quarterly or yearly basis, but is not useful for understanding changes from day to night or any other transients.

With a MAPE of __11.5%__, we've got a ways to go to beat the target of 1.1%.

&nbsp;

#### Prophet

The Prophet package gets mixed reviews in the data science crowd. Some people love it because it is very easy to use, while others hate it precisely because its ease of use leads to misinterpretation of the results it provides. Regardless of your point of view, Prophet does perform well in certain scenarios, like this one, where there is a strong cyclic pattern to the data as well as macro trends. From the visualizations, we can see that Prophet has done a good job capturing the macro trend and has produced a reasonable-looking forecast. Plotting Prophet's predictions against actuals and zooming in, we can see that Prophet has captured the "double-hump" daily pattern and has the flexibility to predict the full magnitude of the daily fluctuations, but simply misses the mark on certain days.

MAPE of __7.02%__ is an improvement over the simple moving average, but nowhere near beating the target. Prophet has the ability to do multi-variate time series, which would give it a better shot, but to keep things fair with the other models, we will keep this analysis to the univariate domain.

&nbsp;

#### LSTM 1
This first iteration of an LSTM model is very basic, just making sure all the model building, training and evaluation pipelines are working properly. A key part of preparing data for an LSTM is the creation of sequences of data for the LSTM to learn. In this iteration, we give it a lookback window of 1, which is essentially no lookback. We build the model with 10 LSTM units, a 0.2 Dropout layer and a Dense layer with one output unit for our next period prediction. We use the Adam optimizer and MSE for the loss function, then train for 10 epochs.

The plot of the losses looks good, with losses decreasing at first, then leveling out. Plotting predictions vs actuals, we see that even this basic LSTM is able to model the timeseries quite accurately. Interestingly, while the predictions are accurate, they seem to be one period behind. This may be due to the lack of lookback, or that the model is simply not predicting, but rather correcting itself at each step.

MAPE is __4.02%__, a significant improvement over the baseline and Prophet. Let's see how much we can improve.


&nbsp;

#### LSTM 2
For the second model, I increased the lookback window to 100 time periods. This should give the LSTM the sequence data it needs to model the time series. I increased the units in the LSTM layer to give it more parameters to handle the increased lookback data. For the first model, the losses started dropping nicely at the beginning of training, but then the gains started to drop off. With the additional trainable parameters in this model, I think we will be able train for longer without seeing the losses flatline, so I extended the training to 50 epochs. I also added an early stopping callback to prevent overfitting.

The loss curves look good. The telltale signs of overfitting (intial drop in validation loss followed by a steady increase, while the training loss continues to drop) are not present, indicating we're still in the productive part of the training curve. Additionally, we did not trip early stopping, which further supports the idea that there is more performance to squeeze out of this model.

Looking at the plot of predictions vs actuals, we can see very good agreement. The one-period offset we saw in the previous model is now gone. This is looking promising.

MAPE of __1.29%__ is a significant improvement over the basic LSTM score, but not yet at the level we're trying to beat.


&nbsp;

#### LSTM 3
In this iteration, I extended the lookback window to 168 periods, which is 7 days. The thinking here is that giving the LSTM an entire week of sequences will help it learn week-to-week patterns in addition to the daily patterns it has already clearly picked up.

Since the last model did not trip the early stopping callback and loss scores continued to improve at 50 epochs, I extended the training to 100 epochs. The early stopping callback is still active to protect us from overfitting. This time we did trip the early stopping at 93 epochs.

MAPE is now __1.07%__, another meaningful improvement, and we're now beating the 1.10% MAPE for the forecast provided by the Spanish power utility, although our 486 MSE is slightly worse than their 455.


&nbsp;

#### LSTM 4
My hunch at this point is the model needs more parameters in order to perform better, so I added a 100-unit Dense layer right after the LSTM layer. The thinking is that similar to a CNN architecture, the LSTM is acting as a feature extractor and the fully connected layer can act as a pattern-recognizer and regressor. With the additional trainable parameters, we went all the way out to 100 epochs without tripping the early stopping callback.

Unfortunately, the MAPE got slightly worse at __1.10%__.



&nbsp;

#### LSTM 5
The last iteration showed some strange behavior of the loss scores where they would repeatedly settle down to a low level, then jump back up, only to settle back down a few epochs later. A possible theory is that the learning rate is too high and the model is jumping from one side of the gradient descent "valley" to the other without being able to settle down to the optimal solution. Or that it is popping out of an optimal solution and into a local minimum. In either case, slowing down the learning rate seemed like a good idea. To do this in the later epochs without slowing down convergence in the early epochs, I implemented an exponential decay learning rate schedule.

After a few attempts with different initial learning rates and decay rates, I settled on 0.001 and 0.98 respectively. This resulted in training going all the way to 100 epochs, but with a much smoother validation loss curve.

It also delivered a MAPE of __1.03%__ and MSE of 465, easily beating the MAPE target and coming very close on MSE.

---
## 6. Conclusion

#### Summary of results

| Model | Architecture | Lookback | LSTM units | Epochs | Learning Rate | MAPE | MSE |
|-----|:-----:|:-------:|:---:|:---:|:---:|---:|---:|
| Target   | unknown    | n/a | n/a | n/a | n/a           | __1.10%__   | 455  |
| Baseline | Moving avg | 30  | n/a | n/a | n/a               | 11.5%   | 3828 |
| Prophet  | Prophet    | n/a | n/a | n/a | n/a               | 7.02%   | 2658 |
| LSTM 1   | LSTM       | 1   | 10  | 10  | Fixed             | 4.02%   | 1432 |
| LSTM 2   | LSTM       | 100 | 100 | 50  | Fixed             | 1.29%   | 551  |
| LSTM 3   | LSTM       | 168 | 100 | 93  | Fixed             | 1.07%   | 486  |
| LSTM 4   | LSTM       | 168 | 100 | 100 | Fixed             | 1.10%   | 479  |
| LSTM 5   | LSTM   | 168 | 100 | 100 | Exponential Decay | __1.03%__   | 465  |

&nbsp;

This was a very enjoyable project and I learned a lot about LSTM and timeseries forecasting. I was pleasantly surprised at how well even a basic LSTM performed. It was quite rewarding to see that despite the high level of performance out of the box, I was able to make significant improvements to the MAPE and MSE scores of my LSTM model.

To further evolve this model I could try a more complicated model with additional LSTM layers, but I think we're approaching the limit of what we can do with this data and this model architecture. In order to improve significantly, I think we will have to bring in more data. I am very interested in multi-variate time series analysis and would be excited to try and bring in weather data like temperature or cloud cover.

It is very satisfying when I can apply my skills as a data scientist to meaningful topics like energy production and consumption. We need more data-driven analysis of this topic to have any hope of transitioning to renewable energy sources and establishing a sustainable relationship with our planet. Thanks for reading.

---
## 7. References

- Kaggle: Hourly energy demand generation and weather. https://www.kaggle.com/datasets/nicholasjhana/energy-consumption-generation-prices-and-weather
- Facebook Prophet: https://facebook.github.io/prophet/
- Keras LSTM: https://keras.io/api/layers/recurrent_layers/lstm/